In [4]:
%pip uninstall openai

^C
Note: you may need to restart the kernel to use updated packages.


In [ ]:
%pip install openai==0.28

In [3]:
%pip install Werkzeug==2.2.2

   ---------------------------------------- 0.0/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   - -------------------------------------- 10.2/232.7 kB ? eta -:--:--
   ------ -------------------------------- 41.0/232.7 kB 115.9 kB/s eta 0:00:02
   ------ -------------------------------- 41.0/232.7 kB 115.9 kB/s eta 0:00:02
   -------------------- ----------------- 122.9/232.7 kB 288.8 kB/s eta 0:00:01
   -------------------- ----------------- 122.9/232.7 kB 288.8 kB/s eta 0:00:01
   -------------------------------------- 232.7/232.7 kB 474.3 kB/s eta 0:00:00
  Attempting uninstall: Werkzeug
    Found existing installation: Werkzeug 3.0.1
    Uninstalling


[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
%pip install Flask==2.0.1 openai openai-whisper gunicorn


ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
googletrans 3.0.0 requires httpx==0.13.3, but you have httpx 0.27.0 which is incompatible.

[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/798.6 kB ? eta -:--:--
     ---------------------------------------- 0.0/

Input Audio Display

In [2]:
from IPython.display import Audio
import numpy as np
import librosa

file_path = r'C:\Users\nisha\Downloads\AB HINDI 2.wav'
audio, sr = librosa.load(file_path, sr=None)

Audio(data=audio, rate=sr)

ASR Model (Automatic Speech Recognition Model)

In [3]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor
import torchaudio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = WhisperProcessor.from_pretrained("openai/whisper-large")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large")


audio_input, sample_rate = torchaudio.load(r"C:\Users\nisha\Downloads\AB HINDI 2.wav")


if sample_rate != 16000:

    resampler = torchaudio.transforms.Resample(sample_rate, 16000)
    audio_input = resampler(audio_input)


input_features = processor(audio_input[0], sampling_rate=16000, return_tensors="pt").input_features


with torch.no_grad():
    predicted_ids = model.generate(input_features)


transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)

print("English Transcription:")
print(transcription[0])
output_file_path = "transcription_output.txt"
with open(output_file_path, "w", encoding="utf-8") as file:
    file.write(transcription[0])

print(f"Transcription saved to: {output_file_path}")


C:\Users\nisha\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Selected GPU: NVIDIA GeForce RTX 3050 Laptop GPU


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


English Transcription:
 Greetings, our country and the whole world are facing the COVID-19 challenge. COVID-19 is not over yet. In such a situation, it is our duty to remain alert. Therefore, until there is no medicine, there is no delay. To save yourself from COVID-19, it is necessary to wash your hands regularly, wear a mask and maintain proper distance between yourself. Remember, a 2-foot distance mask is necessary. If you find it difficult to breathe or have a cough, contact Help Line number 1075.
Transcription saved to: transcription_output.txt


English Transcript to Audio

In [13]:
from transformers import AutoProcessor, AutoModel
from IPython.display import Audio
import torch
import numpy as np

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = AutoProcessor.from_pretrained("suno/bark-small")
model = AutoModel.from_pretrained("suno/bark-small")


input_file_path = r"F:\SIH\Multilingual Speech-to-Text Video Synthesis Platform\transcription_output.txt"  
with open(input_file_path, "r", encoding="utf-8") as file:
    input_text = file.read()


chunk_size = 200  
chunks = [input_text[i:i + chunk_size] for i in range(0, len(input_text), chunk_size)]


audio_chunks = []

for i, chunk in enumerate(chunks):
    print(f"Processing chunk {i + 1}/{len(chunks)}")
    inputs = processor(text=chunk, return_tensors="pt")
    speech_values = model.generate(**inputs, do_sample=True)
    audio_chunks.append(speech_values[0].cpu().numpy().squeeze())


final_audio = np.concatenate(audio_chunks)


sampling_rate = 22050
Audio(final_audio, rate=sampling_rate)


Selected GPU: NVIDIA GeForce RTX 3050 Laptop GPU


'(ReadTimeoutError("HTTPSConnectionPool(host='huggingface.co', port=443): Read timed out. (read timeout=10)"), '(Request ID: 7ed9ba83-f703-4fb7-b645-07a9a2e6b1b3)')' thrown while requesting HEAD https://huggingface.co/suno/bark-small/resolve/main/preprocessor_config.json
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Processing chunk 1/3


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Processing chunk 2/3


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Processing chunk 3/3


French Transcription:

In [1]:
from transformers import WhisperProcessor, WhisperForConditionalGeneration
import torchaudio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = WhisperProcessor.from_pretrained("openai/whisper-large-v2")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v2")
model.config.forced_decoder_ids = processor.get_decoder_prompt_ids(language="french", task="transcribe")


audio_input, sample_rate = torchaudio.load(r"C:\Users\nisha\Downloads\WhatsApp Audio 2023-10-05 at 1.00.46 PM.mpeg")


if sample_rate != 16000:
  
    resampler = torchaudio.transforms.Resample(sample_rate, 16000)
    audio_input = resampler(audio_input)


input_features = processor(audio_input[0], sampling_rate=16000, return_tensors="pt").input_features


with torch.no_grad():
    predicted_ids = model.generate(input_features)


transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)


print("French Transcription:")
print(transcription[0])
output_file_path = "transcription_output_french.txt"
with open(output_file_path, "w", encoding="utf-8") as file:
    file.write(transcription[0])

print(f"Transcription saved to: {output_file_path}")


C:\Users\nisha\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


French Transcription:
 Le train de Mourad Abad de la station de Ahindabad à Sultanpur est en train de partir. Il est à la station 1. Il est à l'invitation des passagers de rester à leur endroit.
Transcription saved to: transcription_output_french.txt


French Transcript to Audio

In [3]:
from transformers import AutoProcessor, AutoModel
from IPython.display import Audio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")

processor = AutoProcessor.from_pretrained("suno/bark-small")
model = AutoModel.from_pretrained("suno/bark-small")


input_file_path = "transcription_output_french.txt"  
with open(input_file_path, "r", encoding="utf-8") as file:
    transcript = file.read().splitlines()


inputs = processor(
    text=transcript,
    return_tensors="pt",
)


speech_values = model.generate(**inputs, do_sample=True, output_attentions=True)


sampling_rate = 22050 


Audio(speech_values[0].cpu().numpy().squeeze(), rate=sampling_rate)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


Spanish Transcription:

In [2]:
from transformers import WhisperProcessor, WhisperForConditionalGeneration
import torchaudio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = WhisperProcessor.from_pretrained("openai/whisper-large-v2")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v2")
model.config.forced_decoder_ids = processor.get_decoder_prompt_ids(language="spanish", task="transcribe")

audio_input, sample_rate = torchaudio.load(r"C:\Users\nisha\Downloads\WhatsApp Audio 2023-10-05 at 1.00.46 PM.mpeg")


if sample_rate != 16000:

    resampler = torchaudio.transforms.Resample(sample_rate, 16000)
    audio_input = resampler(audio_input)


input_features = processor(audio_input[0], sampling_rate=16000, return_tensors="pt").input_features


with torch.no_grad():
    predicted_ids = model.generate(input_features)


transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)


print("Spanish Transcription:")
print(transcription[0])
output_file_path = "transcription_output_spanish.txt"
with open(output_file_path, "w", encoding="utf-8") as file:
    file.write(transcription[0])

print(f"Transcription saved to: {output_file_path}")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Spanish Transcription:
 Por favor, fijarse. En el camino de Muradabad, a través de la Junción de Ahindabad, se encuentra la plataforma número 1 que va a Sultanpur. Se solicita a los pasajeros que se queden en su lugar.
Transcription saved to: transcription_output_spanish.txt


Spanish Transcript to Audio

In [4]:
from transformers import AutoProcessor, AutoModel
from IPython.display import Audio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")

processor = AutoProcessor.from_pretrained("suno/bark-small")
model = AutoModel.from_pretrained("suno/bark-small")


input_file_path = "transcription_output_spanish.txt"  
with open(input_file_path, "r", encoding="utf-8") as file:
    transcript = file.read().splitlines()


inputs = processor(
    text=transcript,
    return_tensors="pt",
)


speech_values = model.generate(**inputs, do_sample=True, output_attentions=True)


sampling_rate = 22050 


Audio(speech_values[0].cpu().numpy().squeeze(), rate=sampling_rate)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:10000 for open-end generation.


In [1]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor
import torchaudio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = WhisperProcessor.from_pretrained("openai/whisper-large")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large")


audio_input, sample_rate = torchaudio.load(r"C:\Users\nisha\Downloads\WhatsApp Audio 2023-10-21 at 7.19.42 PM.mpeg")


if sample_rate != 16000:

    resampler = torchaudio.transforms.Resample(sample_rate, 16000)
    audio_input = resampler(audio_input)


input_features = processor(audio_input[0], sampling_rate=16000, return_tensors="pt").input_features


with torch.no_grad():
    predicted_ids = model.generate(input_features)


transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)

print("English Transcription:")
print(transcription[0])
output_file_path = "transcription_output2.txt"
with open(output_file_path, "w", encoding="utf-8") as file:
    file.write(transcription[0])

print(f"Transcription saved to: {output_file_path}")


C:\Users\nisha\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Selected GPU: NVIDIA GeForce RTX 3050 Laptop GPU


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


English Transcription:
 Thank you for your time and advice. This phone is free of charge and will give you information about the process of asylum. You will not be charged for this period. It is possible that you will be recorded for the purpose of training and training. You will be soon connected to a lawyer and a lawyer. But first we want you to register your wife and her participation in the process.
Transcription saved to: transcription_output2.txt


In [4]:
from transformers import WhisperProcessor, WhisperForConditionalGeneration
import torchaudio
import torch

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = WhisperProcessor.from_pretrained("openai/whisper-large-v2")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v2")
model.config.forced_decoder_ids = processor.get_decoder_prompt_ids(language="panjabi", task="transcribe")

audio_input, sample_rate = torchaudio.load(r"C:\Users\nisha\Downloads\WhatsApp Audio 2023-10-21 at 7.19.42 PM.mpeg")


if sample_rate != 16000:

    resampler = torchaudio.transforms.Resample(sample_rate, 16000)
    audio_input = resampler(audio_input)


input_features = processor(audio_input[0], sampling_rate=16000, return_tensors="pt").input_features


with torch.no_grad():
    predicted_ids = model.generate(input_features)


transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)


print("Spanish Transcription:")
print(transcription[0])
output_file_path = "transcription_output_spanish.txt"
with open(output_file_path, "w", encoding="utf-8") as file:
    file.write(transcription[0])

print(f"Transcription saved to: {output_file_path}")

Selected GPU: NVIDIA GeForce RTX 3050 Laptop GPU


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Spanish Transcription:
 मश्वरा खिदमत ते काल करने दा शुक्रिया। ऐफون ते एक मुफ्त खिदमत है जिरी असाइलम्ब दे अमल दे बारे विच राजदराना मश्वरा ते मालूमात देंती है। इस काल ले तानू चार्ज नहीं किता जाएगा। हो सकता है काल नू तरबियत मियार दे मकसद ले रिकॉर्ड किता जाए। तानू जल्ड एक मशीर ते मतरज्जम नाल मुनसली किता जाएगा। पर पहला आसी चान देयां कि तुसी कवाइफ ते तहफ़फुस
Transcription saved to: transcription_output_spanish.txt


Test file down

In [ ]:
from transformers import AutoProcessor, AutoModel
from IPython.display import Audio
import torch
import numpy as np

selected_gpu_name = torch.cuda.get_device_name(0)
print(f"Selected GPU: {selected_gpu_name}")
torch.device("cuda:0")


processor = AutoProcessor.from_pretrained("suno/bark-small")
model = AutoModel.from_pretrained("suno/bark-small")


input_file_path = r"C:\Users\nisha\Downloads\American's_Choice_and_Opportunity_(Newton_D._Baker).ogg.mp3"
with open(input_file_path, "r", encoding="utf-8") as file:
    input_text = file.read()


chunk_size = 200  
chunks = [input_text[i:i + chunk_size] for i in range(0, len(input_text), chunk_size)]


audio_chunks = []

for i, chunk in enumerate(chunks):
    print(f"Processing chunk {i + 1}/{len(chunks)}")
    inputs = processor(text=chunk, return_tensors="pt")
    speech_values = model.generate(**inputs, do_sample=True)
    audio_chunks.append(speech_values[0].cpu().numpy().squeeze())


final_audio = np.concatenate(audio_chunks)


sampling_rate = 22050
Audio(final_audio, rate=sampling_rate)
